In [1]:
import os
import rasterio                  # I/O raster data (netcdf, height, geotiff, ...)
import rasterio.warp             # Reproject raster samples
from rasterio import windows
import fiona                     # I/O vector data (shape, geojson, ...)
import geopandas as gps

from shapely.geometry import Point, Polygon
from shapely.geometry import mapping, shape

import numpy as np               # numerical array manipulation
import os
from tqdm import tqdm
import PIL.Image
import PIL.ImageDraw
import pandas as pd

from random import shuffle

from itertools import product
from tensorflow.keras.models import load_model


import sys
from core.UNet import UNet
from core.losses import tversky, accuracy, dice_coef, dice_loss, specificity, sensitivity
from core.losses_FTL import focalTversky,accuracy,dice_coef,dice_loss,true_positives,false_positives,true_negatives,false_negatives,sensitivity,specificity,PA,IoU_Pos,IoU_Neg,mIoU,F1_Score

from core.optimizers import adaDelta#, adagrad, adam, nadam
from core.frame_info import FrameInfo, image_normalize
from core.dataset_generator import DataGenerator
from core.split_frames import split_dataset
from core.visualize import display_images

#%matplotlib inline
import matplotlib.pyplot as plt  # plotting tools
import matplotlib.patches as patches
from matplotlib.patches import Polygon

import warnings                  # ignore annoying warnings
warnings.filterwarnings("ignore")
import logging
logger = logging.getLogger()
logger.setLevel(logging.CRITICAL)

import pyproj

#%reload_ext autoreload
#%autoreload 2
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"

import tensorflow as tf
print(tf.__version__)

2.11.0


In [2]:
# Required configurations (including the input and output paths) are stored in a separate file (such as config/RasterAnalysis.py)
# Please provide required info in the file before continuing with this notebook. 
 
from config import RasterAnalysisTestPartOutPut
import random
random.seed(9)
config = RasterAnalysisTestPartOutPut.Configuration()

In [3]:
# Load a pretrained model
OPTIMIZER = adaDelta
model = load_model(config.trained_model_path,
                   custom_objects={'focalTversky': focalTversky, 'dice_coef': dice_coef, 'dice_loss': dice_loss, 
                                   'true_positives': true_positives, 'false_positives': false_positives,
                                   'true_negatives': true_negatives, 'false_negatives': false_negatives, 
                                   'accuracy': accuracy, 'specificity': specificity, 'sensitivity': sensitivity,
                                   'PA': PA, 'IoU_Pos': IoU_Pos, 'IoU_Neg': IoU_Neg, 
                                   'mIoU': mIoU, 'F1_Score': F1_Score}, compile=False)
model.compile(optimizer=OPTIMIZER, loss=focalTversky,
              metrics=[accuracy, dice_coef, dice_loss, true_positives, false_positives, true_negatives, false_negatives,
                       sensitivity, specificity, PA, IoU_Pos, IoU_Neg, mIoU, F1_Score])

In [4]:
# Methods to add results of a patch to the total results of a larger area. The operator could be min (useful if there are too many false positives), max (useful for tackle false negatives)
def addTOResult(res, prediction, row, col, he, wi, operator = 'MAX'):
    currValue = res[row:row+he, col:col+wi]
    newPredictions = prediction[:he, :wi]
# IMPORTANT: MIN can't be used as long as the mask is initialed with 0!!!!! If you want to use MIN initial the mask with -1 and handle the case of default value(-1) separately.
    if operator == 'MIN': # Takes the min of current prediction and new prediction for each pixel
        currValue [currValue == -1] = 1 #Replace -1 with 1 in case of MIN
        resultant = np.minimum(currValue, newPredictions)
    elif operator == 'MAX':
        resultant = np.maximum(currValue, newPredictions)
    else: #operator == 'REPLACE':
        resultant = newPredictions
# Alternative approach; Lets assume that quality of prediction is better in the centre of the image than on the edges
# We use numbers from 1-5 to denote the quality, where 5 is the best and 1 is the worst.In that case, the best result would be to take into quality of prediction based upon position in account
# So for merge with stride of 0.5, for eg. [12345432100000] AND [00000123454321], should be [1234543454321] instead of [1234543214321] that you will currently get.
# However, in case the values are strecthed before hand this problem will be minimized
    res[row:row+he, col:col+wi] =  resultant
    return (res)

In [5]:
def predict_using_model(model, batch, batch_pos, mask, operator):
    tm = np.stack(batch, axis=0)
    prediction = model.predict(tm)
    for i in range(len(batch_pos)):
        (col, row, wi, he) = batch_pos[i]
        p = np.squeeze(prediction[i], axis=-1)
        # Instead of replacing the current values with new values, use the user specified operator (MIN,MAX,REPLACE)
        mask = addTOResult(mask, p, row, col, he, wi, operator)
    return mask

# Methods that actually makes the predictions
def detect_tree(pan_img, width=512, height=512, stride=512, normalize=True):
    # assert ndvi_img.meta['width'] == pan_img.meta['width'] and ndvi_img.meta['height'] == pan_img.meta['height']
    nols, nrows = pan_img.meta['width'], pan_img.meta['height']
    meta = pan_img.meta.copy()
    # print('meta:')
    # print(meta)
    if 'float' not in meta[
        'dtype']:  # The prediction is a float so we keep it as float to be consistent with the prediction.
        meta['dtype'] = np.float32
    offsets = product(range(0, nols, stride), range(0, nrows, stride))
    big_window = windows.Window(col_off=0, row_off=0, width=nols, height=nrows)
    #     print(nrows, nols)

    mask = np.zeros((nrows, nols), dtype=meta['dtype'])

    #     mask = mask -1 # Note: The initial mask is initialized with -1 instead of zero to handle the MIN case (see addToResult)
    batch = []
    batch_pos = []
    for col_off, row_off in tqdm(offsets):
        window = windows.Window(col_off=col_off, row_off=row_off, width=width, height=height).intersection(big_window)
        transform = windows.transform(window, pan_img.transform)
        patch = np.zeros((height, width, 3))  # Add zero padding in case of corner images
        # ndvi_sm = ndvi_img.read(window=window)
        pan_sm = pan_img.read(window=window)
        # temp_im = np.stack((ndvi_sm, pan_sm), axis = -1)
        temp_im = np.stack(pan_sm, axis=-1)
        temp_im = np.squeeze(temp_im)

        if normalize:
            temp_im = image_normalize(temp_im, axis=(
            0, 1))  # Normalize the image along the width and height i.e. independently per channel

        patch[:window.height, :window.width] = temp_im
        batch.append(patch)
        batch_pos.append((window.col_off, window.row_off, window.width, window.height))
        if (len(batch) == config.BATCH_SIZE):
            mask = predict_using_model(model, batch, batch_pos, mask, 'MAX')
            batch = []
            batch_pos = []

    # To handle the edge of images as the image size may not be divisible by n complete batches and few frames on the edge may be left.
    if batch:
        mask = predict_using_model(model, batch, batch_pos, mask, 'MAX')
        batch = []
        batch_pos = []

    return (mask, meta)


In [6]:
schema = {
    'geometry': 'Polygon',
    'properties': {'id': 'str', 'canopy': 'float:15.2', },
}


def drawPolygons(polygons, shape):
    mask = np.zeros(shape, dtype=np.uint8)
    mask = PIL.Image.fromarray(mask)
    draw = PIL.ImageDraw.Draw(mask)
    for polygon in polygons:
        xy = [(point[1], point[0]) for point in polygon]
        draw.polygon(xy=xy, outline=255, fill=255)
    mask = np.array(mask)  # , dtype=bool)
    return (mask)


def transformToXY(polygons, transform):
    tp = []
    for polygon in polygons:
        rows, cols = zip(*polygon)
        x, y = rasterio.transform.xy(transform, rows, cols)
        tp.append(list(zip(x, y)))
    return (tp)


def createShapefileObject(polygons, meta, wfile):
    with fiona.open(wfile, 'w', crs=meta.get('crs').to_dict(), driver='ESRI Shapefile', schema=schema) as sink:
        for idx, mp in enumerate(polygons):
            try:
                #                 poly = Polygon(poly)
                #             assert mp.is_valid
                #             assert mp.geom_type == 'Polygon'
                sink.write({
                    'geometry': mapping(mp),
                    'properties': {'id': str(idx), 'canopy': mp.area},
                })
            except:
                print("An exception occurred in createShapefileObject; Polygon must have more than 2 points")


#                 print(mp)

# Generate a mask with polygons
def transformContoursToXY(contours, transform=None):
    tp = []
    for cnt in contours:
        pl = cnt[:, 0, :]
        cols, rows = zip(*pl)
        x, y = rasterio.transform.xy(transform, rows, cols)
        tl = [list(i) for i in zip(x, y)]
        tp.append(tl)
    return (tp)


def mask_to_polygons(maskF, transform):
    # first, find contours with cv2: it's much faster than shapely
    th = 0.5
    mask = maskF.copy()
    mask[mask < th] = 0
    mask[mask >= th] = 1
    mask = ((mask) * 255).astype(np.uint8)
    contours, hierarchy = cv2.findContours(mask, cv2.RETR_TREE, cv2.CHAIN_APPROX_NONE)

    # Convert contours from image coordinate to xy coordinate
    contours = transformContoursToXY(contours, transform)
    if not contours:  # TODO: Raise an error maybe
        print('Warning: No contours/polygons detected!!')
        return [Polygon()]
    # now messy stuff to associate parent and child contours
    cnt_children = defaultdict(list)
    child_contours = set()
    assert hierarchy.shape[0] == 1
    # http://docs.opencv.org/3.1.0/d9/d8b/tutorial_py_contours_hierarchy.html
    for idx, (_, _, _, parent_idx) in enumerate(hierarchy[0]):
        if parent_idx != -1:
            child_contours.add(idx)
            cnt_children[parent_idx].append(contours[idx])

    # create actual polygons filtering by area (removes artifacts)
    all_polygons = []

    for idx, cnt in enumerate(contours):
        if idx not in child_contours:  # and cv2.contourArea(cnt) >= min_area: #Do we need to check for min_area??
            try:
                poly = Polygon(
                    shell=cnt,
                    holes=[c for c in cnt_children.get(idx, [])])
                # if cv2.contourArea(c) >= min_area]) #Do we need to check for min_area??
                all_polygons.append(poly)
            except:
                pass
    #                 print("An exception occurred in createShapefileObject; Polygon must have more than 2 points")
    print(len(all_polygons))
    return (all_polygons)


def create_contours_shapefile(mask, meta, out_fn):
    res = mask_to_polygons(mask, meta['transform'])
    #     res = transformToXY(contours, meta['transform'])
    createShapefileObject(res, meta, out_fn)


def writeMaskToDisk(detected_mask, detected_meta,pan, wp, write_as_type='uint8', th=0, create_countors=False):
    # Convert to correct required before writing
    if 'float' in str(detected_meta['dtype']) and 'int' in write_as_type:
        print(f'Converting prediction from {detected_meta["dtype"]} to {write_as_type}, using threshold of {th}')
        
        print(detected_mask)
        
        detected_mask[detected_mask < th] = 0
        detected_mask[detected_mask >= th] = 1
        
        detected_mask = detected_mask.astype(write_as_type)

        #
        pan_arr = pan.read()


        print(detected_mask.shape)
        #         ndvi_arr=np.squeeze(ndvi_arr, axis=0)
        pan_arr[0][detected_mask == 0] = np.nan
        pan_arr[0][pan_arr[0] == 0] = np.nan

        pan_arr[1][detected_mask == 0] = np.nan
        pan_arr[1][pan_arr[1] == 0] = np.nan

        pan_arr[2][detected_mask == 0] = np.nan
        pan_arr[2][pan_arr[2] == 0] = np.nan


        valid_mask = np.any(~np.isnan(pan_arr), axis=0).astype(np.uint8)

        detected_mask = detected_mask.astype(write_as_type)
        detected_meta['dtype'] = write_as_type
        detected_meta['count'] = 1
        target_crs = pyproj.CRS('EPSG:3857')
        detected_meta['crs'] = target_crs
            #break
        print(valid_mask)
        #print(valid_mask.shape)
        is_all_zeros =np.all(valid_mask == 0)
        if is_all_zeros :
            pass
        else:
            with rasterio.open(wp, 'w', **detected_meta) as outds:
                outds.write(valid_mask,1)
            if create_countors:
                wp = wp.replace(image_type, output_shapefile_type)
                create_contours_shapefile(detected_mask, detected_meta, wp)

In [7]:
all_files = []
for root, dirs, files in os.walk(config.input_image_dir):
    files.sort()
    for file in files:
        if file.endswith(config.input_image_type) and file.startswith(config.pan_fn_st):
             all_files.append((os.path.join(root, file), file))
                
                
print(all_files)
print('FINISH')


#shuffle(all_files)

for idx, (fullPath, filename) in enumerate(all_files):
    #a_lb_path, a_lb_fn = all_annotations[idx]
    #w_lb_path, w_lb_fn = all_weights[idx]
    outputFile = os.path.join(config.output_dir, filename.replace(config.pan_fn_st, config.output_prefix))
    if not os.path.isfile(outputFile) or config.overwrite_analysed_files:  # isfile function check whether the path is existing or not
        with rasterio.open(fullPath) as pan:
            print(pan)
            detectedMask, detectedMeta = detect_tree(pan, width=config.WIDTH, height=config.HEIGHT,
                                                     stride=config.STRIDE,
                                                     normalize=False)  # WIDTH and HEIGHT should be the same and in this case Stride is 50 % width
            #
            # # Write the mask to file
            # #                 if station_name == 'Dungeness' and time_str == '19890630':
            writeMaskToDisk(detectedMask, detectedMeta,pan,outputFile, write_as_type=config.output_dtype, th=0.5,create_countors=False)
            #writeMaskToDisk(idx, lon, lat, ndvi, label, station_name, time_str, detectedMask, detectedMeta,outputFile, write_as_type=config.output_dtype, th=0.5, create_countors=False)

    else:
        print('File already analysed!', fullPath)


[('E:\\ACM\\Final_ChongCi\\FinalOutPut\\TestPartResult0930_0825_New\\pan_333_0.tif', 'pan_333_0.tif'), ('E:\\ACM\\Final_ChongCi\\FinalOutPut\\TestPartResult0930_0825_New\\pan_333_1.tif', 'pan_333_1.tif'), ('E:\\ACM\\Final_ChongCi\\FinalOutPut\\TestPartResult0930_0825_New\\pan_333_10.tif', 'pan_333_10.tif'), ('E:\\ACM\\Final_ChongCi\\FinalOutPut\\TestPartResult0930_0825_New\\pan_333_100.tif', 'pan_333_100.tif'), ('E:\\ACM\\Final_ChongCi\\FinalOutPut\\TestPartResult0930_0825_New\\pan_333_1000.tif', 'pan_333_1000.tif'), ('E:\\ACM\\Final_ChongCi\\FinalOutPut\\TestPartResult0930_0825_New\\pan_333_1001.tif', 'pan_333_1001.tif'), ('E:\\ACM\\Final_ChongCi\\FinalOutPut\\TestPartResult0930_0825_New\\pan_333_1002.tif', 'pan_333_1002.tif'), ('E:\\ACM\\Final_ChongCi\\FinalOutPut\\TestPartResult0930_0825_New\\pan_333_1003.tif', 'pan_333_1003.tif'), ('E:\\ACM\\Final_ChongCi\\FinalOutPut\\TestPartResult0930_0825_New\\pan_333_1004.tif', 'pan_333_1004.tif'), ('E:\\ACM\\Final_ChongCi\\FinalOutPut\\TestPa

1it [00:00, 125.11it/s]


1/1 [==============================] - 2s 2s/step
Converting prediction from float32 to uint8, using threshold of 0.5
[[1.6214062e-05 2.8017777e-08 2.4296565e-09 ... 1.5530947e-13
  2.8127821e-11 5.3732418e-07]
 [5.7856479e-08 3.5993448e-12 4.7799347e-14 ... 4.0037807e-27
  1.2389877e-22 2.8515048e-13]
 [1.2528772e-08 2.8323432e-13 1.5652174e-15 ... 2.0577303e-37
  2.4247357e-31 9.9024314e-18]
 ...
 [3.3076618e-11 1.2824632e-16 4.0390820e-18 ... 6.9793143e-16
  3.1137937e-14 9.9783681e-10]
 [4.9524140e-10 8.2307386e-15 5.9429579e-16 ... 3.1668190e-14
  1.0203512e-12 9.1393089e-09]
 [9.7617271e-07 6.9822381e-10 1.0885320e-10 ... 7.3369721e-10
  1.0719063e-08 4.2463166e-06]]
(512, 512)
[[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 ...
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]
<open DatasetReader name='E:/ACM/Final_ChongCi/FinalOutPut/TestPartResult0930_0825_New/pan_333_1.tif' mode='r'>


1it [00:00,  8.57it/s]


1/1 [==============================] - 1s 966ms/step
Converting prediction from float32 to uint8, using threshold of 0.5
[[2.71519311e-05 3.81470429e-08 4.89518603e-09 ... 4.80761519e-09
  4.54335556e-08 1.93981377e-05]
 [2.85235515e-08 8.13001684e-13 4.83244324e-14 ... 1.98069697e-15
  1.03121328e-13 3.84190946e-09]
 [1.19303225e-08 2.71190947e-13 1.11023615e-14 ... 2.04495501e-19
  5.13181231e-17 4.25406169e-11]
 ...
 [3.47181395e-10 1.06786206e-15 9.69513250e-18 ... 9.70595083e-23
  6.13665237e-19 1.06117606e-11]
 [1.11103606e-08 2.84307083e-13 7.42001370e-15 ... 6.90111777e-21
  1.80034322e-17 6.63216773e-11]
 [1.63466066e-05 2.41186751e-08 2.66118216e-09 ... 4.38778720e-14
  7.56513081e-12 1.39939729e-07]]
(512, 512)
[[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 ...
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]
<open DatasetReader name='E:/ACM/Final_ChongCi/FinalOutPut/TestPartResult0930_0825_New/pan_333_10.tif' mode='r'>


...

1/1 [==============================] - 1s 1s/step
Converting prediction from float32 to uint8, using threshold of 0.5
[[4.09511358e-06 1.69850767e-09 7.70738751e-11 ... 4.40134418e-09
  1.02535786e-07 4.12792651e-05]
 [8.51171855e-10 3.36273033e-15 3.13325858e-17 ... 3.22511013e-15
  7.21913523e-13 1.96440944e-08]
 [7.49957943e-11 8.69607037e-17 2.00875551e-19 ... 8.55360330e-19
  1.13705417e-15 4.50804616e-10]
 ...
 [2.69359656e-11 1.94783845e-17 3.99401671e-20 ... 1.66640590e-16
  6.06597224e-14 3.55348329e-09]
 [2.53345456e-09 2.94600092e-14 3.28222567e-16 ... 3.09273989e-14
  3.09443074e-12 3.43421149e-08]
 [9.10524977e-06 9.97972460e-09 7.07632952e-10 ... 6.87255974e-10
  1.87486382e-08 8.81243068e-06]]
(512, 512)
[[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 ...
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]
<open DatasetReader name='E:/ACM/Final_ChongCi/FinalOutPut/TestPartResult0930_0825_New/pan_333_998.tif' mode='r'>


1it [00:00, 142.84it/s]


1/1 [==============================] - 1s 1s/step
Converting prediction from float32 to uint8, using threshold of 0.5
[[4.4490994e-06 5.0370788e-09 2.3099493e-10 ... 1.6590407e-10
  2.7499338e-09 3.0363974e-06]
 [6.2517302e-09 1.3846271e-13 6.4054093e-16 ... 1.0664733e-16
  8.8788323e-15 5.6736082e-10]
 [6.0870903e-10 2.6244776e-15 3.4963609e-18 ... 2.7023851e-19
  4.5102575e-17 1.6516831e-11]
 ...
 [2.3637349e-11 4.2548437e-17 1.2621307e-19 ... 2.4060212e-17
  5.8237687e-15 5.8151595e-10]
 [2.8181968e-10 2.7228482e-15 4.7435079e-17 ... 4.3868645e-15
  3.7423390e-13 6.6181096e-09]
 [5.0893414e-07 2.4029526e-10 2.1219120e-11 ... 2.9533828e-10
  6.6397936e-09 3.3018225e-06]]
(512, 512)
[[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 ...
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]
<open DatasetReader name='E:/ACM/Final_ChongCi/FinalOutPut/TestPartResult0930_0825_New/pan_333_999.tif' mode='r'>


1it [00:00, 21.02it/s]


1/1 [==============================] - 1s 1s/step
Converting prediction from float32 to uint8, using threshold of 0.5
[[8.0121472e-06 1.1532165e-08 6.9466916e-10 ... 9.0912584e-23
  2.9814493e-18 1.3465955e-10]
 [1.8996145e-08 7.3508566e-13 5.5138334e-15 ... 0.0000000e+00
  9.9538951e-34 3.5349158e-19]
 [3.0512000e-09 3.2998804e-14 9.5418798e-17 ... 0.0000000e+00
  0.0000000e+00 1.3981926e-26]
 ...
 [8.8776986e-11 4.1456574e-16 2.7957952e-18 ... 2.3635036e-16
  3.5030833e-14 1.8419553e-09]
 [7.9117618e-10 1.5464282e-14 4.5970241e-16 ... 2.3977099e-14
  1.4862315e-12 1.6307441e-08]
 [8.7580037e-07 6.6253686e-10 7.4602748e-11 ... 7.8169327e-10
  1.5121321e-08 6.0401621e-06]]
(512, 512)
[[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 ...
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]
